In [1]:
import pandas as pd
import ast
from tqdm import tqdm
tqdm.pandas()

In [2]:
# Load Data
df_yake_claims = pd.read_json('/mnt/hdd01/patentsview/Patentsview - Cleantech Patents/Cleantech Concepts/Yake/g_patent_claims_cleantech_yake.json')

In [3]:
# Iterate over rows in dataframe
for index, row in tqdm(df_yake_claims.iterrows()):
    # Cast row 'keywords_yake' column to string
    row['keywords_yake'] = str(row['keywords_yake'])
    # Check if keywords_yake column starts with "[[[" and ends with "]]]""
    if row['keywords_yake'].startswith('[[[') and row['keywords_yake'].endswith(']]]'):
        # Remove first "[" and last "]" from keywords_yake column
        row['keywords_yake'] = row['keywords_yake'][1:-1]
    # Cast row 'keywords_yake' column to list
    row['keywords_yake'] = ast.literal_eval(row['keywords_yake'])
    # Assign modified 'keywords_yake' list to temporary variable
    keywords_yake_temp = row['keywords_yake']
    # Assign temporary variable to 'keywords_yake' column
    df_yake_claims.at[index, 'keywords_yake'] = keywords_yake_temp

515742it [01:11, 7168.69it/s]


In [4]:
df_yake_claims['keywords_yake_exploded'] = ''

# Iterate over rows in dataframe
for index,row in tqdm(df_yake_claims.iterrows()):
    # Check if 'keywords_yake' column is not a list
    if not isinstance(row['keywords_yake'], list):
        continue
    # Check if 'keywords_yake' column is an empty list or contains only empty lists
    if not any(keyword for keyword in row['keywords_yake']):
        continue
    # Iterate over keywords in 'keywords_yake' column and append to 'keywords_yake_exploded' column
    else:
        for keyword in row['keywords_yake']:
            df_yake_claims.at[index, 'keywords_yake_exploded'] += keyword[0] + ', '

515742it [02:04, 4145.56it/s]


In [5]:
# Cast 'keywords_yake_exploded' column to list
df_yake_claims['keywords_yake_exploded'] = df_yake_claims['keywords_yake_exploded'].str.split(', ')

In [6]:
# Delete last item in 'keywords_yake_exploded' cells
df_yake_claims['keywords_yake_exploded'] = df_yake_claims['keywords_yake_exploded'].apply(lambda x: x[:-1])

# Postprocessing

In [7]:
keywords_list = []
# Iterate over rows in dataframe
for index,row in tqdm(df_yake_claims.iterrows()):
    # Append 'keywords_yake_exploded' to keywords_list
    keywords_list += row['keywords_yake_exploded']

515742it [00:12, 40351.89it/s]


In [8]:
# Generate unique list of keywords
keywords_list_unique = list(set(keywords_list))
df_keywords_list_unique = pd.DataFrame(keywords_list_unique, columns=['keyword_yake'])

In [9]:
# Count absolute frequency of each keyword
from collections import Counter

# Step 1: Flatten the list of keywords into a single list
flattened_keywords = [keyword for keyword_list in tqdm(df_yake_claims['keywords_yake_exploded']) for keyword in keyword_list]

# Step 2: Use collections.Counter to count the occurrences of each keyword
keyword_counts = Counter(flattened_keywords)

# Step 3: Convert the keyword counts to a DataFrame
count_df = pd.DataFrame(keyword_counts.items(), columns=['keyword_yake', 'abs_frequency'])

# Step 4: Merge the count_df with df_keywords_list_unique on the 'keyword_yake' column
df_keywords_list_unique = df_keywords_list_unique.merge(count_df, on='keyword_yake', how='left')

100%|██████████| 515742/515742 [00:00<00:00, 2654356.85it/s]


In [10]:
### MAYBE I NEED TO REDO THIS WITH FULL TEXT CLAIMS INSTEAD OF JUST THE YAKE KEYWORDS

# Calculate document frequency by dividing absolute frequency by len of df_yake_claims
df_keywords_list_unique['doc_frequency'] = df_keywords_list_unique['abs_frequency'] / len(df_yake_claims)

In [11]:
# Prune dataframe by document frequency and absolute frequency
min_abs_frequency = 10
max_doc_frequency = 0.3

df_keywords_list_unique_pruned = df_keywords_list_unique[(df_keywords_list_unique['abs_frequency'] >= min_abs_frequency) & (df_keywords_list_unique['doc_frequency'] <= max_doc_frequency)]

# Reset index
df_keywords_list_unique_pruned.reset_index(drop=True, inplace=True)

In [12]:
# Only consider n-grams with n >= 2
min_ngram_length = 2

# Generate copy of df_keywords_list_unique_pruned
df_keywords_list_unique_pruned = df_keywords_list_unique_pruned.copy()

def filter_keywords(keyword_string):
    # Split the keyword string into individual keywords
    keywords = keyword_string.split(', ')
    # Filter out keywords with fewer than 2 words
    filtered_keywords = [keyword for keyword in keywords if len(keyword.split()) >= min_ngram_length]
    # Join the filtered keywords back into a string
    return ', '.join(filtered_keywords)

# Create a copy of df_keywords_list_unique_pruned to avoid SettingWithCopyWarning
df_keywords_list_unique_pruned = df_keywords_list_unique_pruned.copy()

# Now use .loc to modify the 'keyword_yake' column
df_keywords_list_unique_pruned.loc[:, 'keyword_yake'] = df_keywords_list_unique_pruned['keyword_yake'].progress_apply(filter_keywords)

# Delete rows with empty 'keyword_yake' column
df_keywords_list_unique_pruned = df_keywords_list_unique_pruned[df_keywords_list_unique_pruned['keyword_yake'] != '']

# Reset index
df_keywords_list_unique_pruned.reset_index(drop=True, inplace=True)

100%|██████████| 32749/32749 [00:00<00:00, 1001284.87it/s]


In [13]:
import nltk
from nltk.corpus import stopwords

# Download stopwords
# nltk.download('stopwords')

# Generate copy of df_keywords_list_unique_pruned
df_keywords_list_unique_pruned = df_keywords_list_unique_pruned.copy()

# Delete all stopwords from 'keyword_yake' column
df_keywords_list_unique_pruned.loc[:, 'keyword_yake'] = df_keywords_list_unique_pruned['keyword_yake'].progress_apply(
    lambda x: ' '.join([word for word in x.split() if word not in (stopwords.words('english'))])
)

100%|██████████| 24789/24789 [00:02<00:00, 8367.10it/s]


In [14]:
### MAYBE I NEED TO REDO THIS PART WITH THE CLAIM TEXTS INSTEAD OF THE KEYWORDS

import spacy

# Download spacy model
nlp = spacy.load('en_core_web_sm')

# Ensure you're working on a new DataFrame, not a slice of an old one
df_keywords_list_unique_pruned_pos = df_keywords_list_unique_pruned.copy()

# Perform part-of-speech tagging on the 'keyword_yake' column 
# and save the POS tags in a new column 'keyword_yake_pos'
df_keywords_list_unique_pruned_pos['keyword_yake_pos'] = df_keywords_list_unique_pruned_pos['keyword_yake'].progress_apply(
    lambda x: [token.pos_ for token in nlp(x)]
)

100%|██████████| 24789/24789 [00:48<00:00, 513.98it/s]


In [15]:
# Filter out all keywords that do not contain NOUN, PRON or PROPN in their POS tags
df_keywords_list_unique_pruned_pos = df_keywords_list_unique_pruned_pos[df_keywords_list_unique_pruned_pos['keyword_yake_pos'].progress_apply(
    lambda x: any(pos in ['NOUN', 'PRON', 'PROPN'] for pos in x)
)]

# Reset index
df_keywords_list_unique_pruned_pos.reset_index(drop=True, inplace=True)

100%|██████████| 24789/24789 [00:00<00:00, 587754.54it/s]


# Keyword Embedding

In [16]:
from sentence_transformers import SentenceTransformer
import torch

/home/thiesen/Documents/Cleantech_Concepts/venv/lib64/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [17]:
# model_climatebert = SentenceTransformer('climatebert/distilroberta-base-climate-f')
# model_bertforpatents = SentenceTransformer('anferico/bert-for-patents')
model_patentsberta = SentenceTransformer('AI-Growth-Lab/PatentSBERTa')

In [18]:
# Check if GPU is available
if torch.cuda.is_available():
    device = torch.device("cuda")
    print("GPU available: {}".format(torch.cuda.get_device_name(0)))
else:
    device = torch.device("cpu")
    print("GPU not available, CPU used")

GPU available: NVIDIA RTX A4500


In [19]:
# Generate copy of df_keywords_list_unique_pruned_pos
df_keywords_list_unique_pruned_embeddings = df_keywords_list_unique_pruned_pos.copy()

# Perform sentence embedding on the 'keyword_yake' column
df_keywords_list_unique_pruned_embeddings['keyword_yake_patentsberta_embedding'] = df_keywords_list_unique_pruned_embeddings['keyword_yake'].progress_apply(
    lambda x: model_patentsberta.encode(x)
)

100%|██████████| 23742/23742 [02:48<00:00, 141.26it/s]


In [ ]:
# Save dataframe to json
df_keywords_list_unique_pruned_embeddings.to_json('/mnt/hdd01/patentsview/Patentsview - Cleantech Patents/Cleantech Concepts/Yake/g_patent_claims_cleantech_yake_keywords_embeddings.json')

# Dimensionality Reduction

In [4]:
# Load data if necessary
df_keywords_list_unique_pruned_embeddings = pd.read_json('/mnt/hdd01/patentsview/Patentsview - Cleantech Patents/Cleantech Concepts/Yake/g_patent_claims_cleantech_yake_keywords_embeddings.json')

## UMAP

In [2]:
import umap
import numpy as np
umap_dim = 2
reducer = umap.UMAP(random_state=42, n_components=umap_dim)

/home/thiesen/Documents/Cleantech_Concepts/venv/lib64/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [5]:
# Stack all the embeddings into a 2D array
embeddings_patentsberta = np.vstack(df_keywords_list_unique_pruned_embeddings['keyword_yake_patentsberta_embedding'].values)

# Perform UMAP dimensionality reduction
umap_embeddings_patentsberta = reducer.fit_transform(embeddings_patentsberta)

# Assign the reduced dimension embeddings back to new DataFrame columns
df_keywords_list_unique_pruned_embeddings['keyword_yake_patentsberta_embedding_umap'] = list(umap_embeddings_patentsberta)

/home/thiesen/Documents/Cleantech_Concepts/venv/lib64/python3.11/site-packages/umap/umap_.py:1943: UserWarning: n_jobs value -1 overridden to 1 by setting random_state. Use no seed for parallelism.
  warn(f"n_jobs value {self.n_jobs} overridden to 1 by setting random_state. Use no seed for parallelism.")


## t-SNE

In [20]:
import numpy as np
from openTSNE import TSNE
from sklearn.model_selection import train_test_split

In [21]:
# Generate train/test split
patentsberta_x_train, patentsberta_x_test = train_test_split(df_keywords_list_unique_pruned_embeddings['keyword_yake_patentsberta_embedding'].tolist(), test_size=0.2, random_state=42)
patentsberta_x_train_np = np.array(patentsberta_x_train)
patentsberta_x_test_np = np.array(patentsberta_x_test)

In [22]:
tsne = TSNE(
    perplexity=30,
    metric="euclidean",
    n_jobs=8,
    random_state=42,
    n_iter=1000,
    verbose=True,
)

In [23]:
# Perform t-SNE on training data
patentsberta_embedding_train = tsne.fit(patentsberta_x_train_np)

--------------------------------------------------------------------------------
TSNE(early_exaggeration=12, n_iter=1000, n_jobs=8, random_state=42,
     verbose=True)
--------------------------------------------------------------------------------
===> Finding 90 nearest neighbors using Annoy approximate search using euclidean distance...
   --> Time elapsed: 10.69 seconds
===> Calculating affinity matrix...
   --> Time elapsed: 0.12 seconds
===> Calculating PCA-based initialization...
   --> Time elapsed: 0.31 seconds
===> Running optimization with exaggeration=12.00, lr=1582.75 for 250 iterations...
Iteration   50, KL divergence 5.9800, 50 iterations in 0.5832 sec
Iteration  100, KL divergence 6.0134, 50 iterations in 0.5701 sec
Iteration  150, KL divergence 6.0139, 50 iterations in 0.5676 sec
Iteration  200, KL divergence 6.0139, 50 iterations in 0.5715 sec
Iteration  250, KL divergence 6.0139, 50 iterations in 0.5607 sec
   --> Time elapsed: 2.85 seconds
===> Running optimization 

In [24]:
patentsberta_embedding_test = patentsberta_embedding_train.transform(patentsberta_x_test_np)

===> Finding 15 nearest neighbors in existing embedding using Annoy approximate search...
   --> Time elapsed: 0.92 seconds
===> Calculating affinity matrix...
   --> Time elapsed: 0.01 seconds
===> Running optimization with exaggeration=4.00, lr=0.10 for 0 iterations...
   --> Time elapsed: 0.00 seconds
===> Running optimization with exaggeration=1.50, lr=0.10 for 250 iterations...
Iteration   50, KL divergence 59103.3439, 50 iterations in 0.9047 sec
Iteration  100, KL divergence 58556.2926, 50 iterations in 0.7862 sec
Iteration  150, KL divergence 58342.3685, 50 iterations in 0.7785 sec
Iteration  200, KL divergence 58238.5809, 50 iterations in 0.7794 sec
Iteration  250, KL divergence 58148.0518, 50 iterations in 0.7796 sec
   --> Time elapsed: 4.03 seconds


In [25]:
patentsberta_embedding = np.concatenate((patentsberta_embedding_train, patentsberta_embedding_test), axis=0)
df_keywords_list_unique_pruned_embeddings['keyword_yake_patentsberta_embedding_tsne'] = patentsberta_embedding.tolist()
df_keywords_list_unique_pruned_embeddings['keyword_yake_patentsberta_embedding_tsne_x'] = df_keywords_list_unique_pruned_embeddings['keyword_yake_patentsberta_embedding_tsne'].apply(lambda x: x[0])
df_keywords_list_unique_pruned_embeddings['keyword_yake_patentsberta_embedding_tsne_y'] = df_keywords_list_unique_pruned_embeddings['keyword_yake_patentsberta_embedding_tsne'].apply(lambda x: x[1])

# Clustering

In [26]:
# Import HDBSCAN
import hdbscan

In [7]:
# Extract UMAP embeddings into 'umap_dim' number of columns dynamically
for i in range(umap_dim):
    df_keywords_list_unique_pruned_embeddings['keyword_yake_patentsberta_embedding_umap_' + str(i)] = df_keywords_list_unique_pruned_embeddings['keyword_yake_patentsberta_embedding_umap'].apply(lambda x: x[i])

In [27]:
# Ensure you're working on a new DataFrame, not a slice of an old one
df_keywords_list_unique_pruned_embeddings_hdbscan = df_keywords_list_unique_pruned_embeddings.copy()

# Perform HDBSCAN clustering on the UMAP coordinates
clusterer_patentsberta = hdbscan.HDBSCAN(min_cluster_size=100, min_samples=1).fit(df_keywords_list_unique_pruned_embeddings_hdbscan[['keyword_yake_patentsberta_embedding_tsne_x', 'keyword_yake_patentsberta_embedding_tsne_y']])

# Assign the cluster labels back to the DataFrame
df_keywords_list_unique_pruned_embeddings_hdbscan['patentsberta_cluster'] = clusterer_patentsberta.labels_

# Erase all rows with cluster -1
df_keywords_list_unique_pruned_embeddings_hdbscan = df_keywords_list_unique_pruned_embeddings_hdbscan[df_keywords_list_unique_pruned_embeddings_hdbscan['patentsberta_cluster'] != -1]

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

In [ ]:
df_keywords_list_unique_pruned_embeddings.to_json('/mnt/hdd01/patentsview/Patentsview - Cleantech Patents/Cleantech Concepts/Yake/g_patent_claims_cleantech_yake_keywords_embeddings_tsne.json')

# Plotting

In [28]:
import plotly.express as px

In [32]:
# Plot the UMAP embeddings in three figures, color coded by cluster
fig_patentsberta = px.scatter(
    df_keywords_list_unique_pruned_embeddings_hdbscan, 
    x='keyword_yake_patentsberta_embedding_tsne_x', 
    y='keyword_yake_patentsberta_embedding_tsne_y', 
    color='patentsberta_cluster', 
    hover_data=['patentsberta_cluster', 'keyword_yake'], 
    title='Cleantech Yake Keywords - HDBSCAN, TSNE, PatentSBERTa',
    height=800,  # Adjust as needed
    width=800    # Adjust as needed
)
# Display the figures
fig_patentsberta.show()

# fig_patentsberta.write_html('/mnt/hdd01/patentsview/Patentsview - Cleantech Patents/Cleantech Concepts/Yake/g_patent_claims_cleantech_yake_keywords_embeddings_tsne.html')

# Name Cluster

In [34]:
from transformers import pipeline, set_seed

In [75]:
# Build dataframe of keywords and their corresponding clusters, where each row is a cluster with list of keywords
df_keywords_clusters_patentsberta = df_keywords_list_unique_pruned_embeddings_hdbscan.groupby('patentsberta_cluster')['keyword_yake'].apply(list).reset_index(name='keywords')

In [35]:
# Initialize a text-generation pipeline with Flan-T5-large
import torch
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
generator = pipeline('text2text-generation', model='google/flan-t5-large', device=device)
set_seed(42)

In [95]:
def generate_cluster_name(keywords):
    # Ensure the keywords are in a list format
    keywords = keywords.split(', ') if isinstance(keywords, str) else keywords
    # Select only the first 1500 keywords from the list
    selected_keywords = keywords[:1500]
    # Join the selected keywords into a string format
    keywords_str = ', '.join(selected_keywords)
    # Create a prompt from the selected keywords
    prompt = f"Come up with a precise and short topic name for the following keywords: {keywords_str}"
    # Generate a response using the GPT-3 model
    response = generator(prompt, max_length=10, do_sample=True, temperature=0.8)[0]['generated_text']
    # Extract the cluster name from the response
    cluster_name = response
    return cluster_name

# Apply the function to the 'keywords' column to generate cluster names
df_keywords_clusters_patentsberta['cluster_name'] = df_keywords_clusters_patentsberta['keywords'].progress_apply(generate_cluster_name)

  0%|          | 0/78 [00:00<?, ?it/s]/home/thiesen/Documents/Cleantech_Concepts/venv/lib64/python3.11/site-packages/transformers/pipelines/base.py:1101: UserWarning:

You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset

100%|██████████| 78/78 [00:20<00:00,  3.82it/s]


In [96]:
# Merge df_keywords_clusters_patentsberta with df_keywords_list_unique_pruned_embeddings_hdbscan on 'patentsberta_cluster'
df_keywords_list_unique_pruned_embeddings_hdbscan = df_keywords_list_unique_pruned_embeddings_hdbscan.merge(df_keywords_clusters_patentsberta[['patentsberta_cluster', 'cluster_name']], on='patentsberta_cluster', how='left')

In [100]:
# Plotting
fig_patentsberta_cluster = px.scatter(
    df_keywords_list_unique_pruned_embeddings_hdbscan, 
    x='keyword_yake_patentsberta_embedding_tsne_x', 
    y='keyword_yake_patentsberta_embedding_tsne_y', 
    color='cluster_name_y', 
    hover_data=['patentsberta_cluster', 'keyword_yake'], 
    title='Cleantech Yake Keywords - HDBSCAN, TSNE, PatentSBERTa',
    height=800,  # Adjust as needed
    width=1200    # Adjust as needed
)

# Display the figures
fig_patentsberta_cluster.show()